In [30]:
import os
import jieba.posseg as psg

In [31]:
file_path='data/train_TBM_checked_new.txt'
dev_path = 'data/development_2.txt'
test_path = 'data/test.txt'

data_path='data/train1_yo.data'
tdata_path='data/test.data'
devpath='data/dev.data'

train_type = 'data/train_yo.type'
test_type = 'data/test.type'
dev_type = 'data/dev.type'

In [32]:
def loadInputFile(path):
    trainingset = []  # store trainingset [content,content,...]
    position = []  # store position [article_id, start_pos, end_pos, entity_text, entity_type, ...]
    mentions = {}  # store mentions[mention] = Type
    
    with open(path, 'r', encoding='utf8') as f:
        file_text=f.read().encode('utf-8').decode('utf-8-sig')
    
    datas=file_text.split('\n\n--------------------\n\n')[:-1]
#     print(datas)
    for data in datas:
        if path == 'data/test.txt':
            data = data.split('\n')[1]
        data=data.split('\n')
        content=data[0]
        trainingset.append(content)
        annotations=data[1:]
        for annot in annotations[1:]:
            annot=annot.split('\t') #annot= article_id, start_pos, end_pos, entity_text, entity_type
            position.extend(annot)
            mentions[annot[3]]=annot[4]
    return trainingset, position, mentions

In [33]:
def pos2dict(pos):
    d_pos = []
    temp = []
    count = 0
    for i in range(0, len(pos), 5):
        if pos[i] == str(count):
            temp.append(pos[i] + ' ' + pos[(i+1)] + ' ' + pos[(i+2)] + ' ' + pos[(i+3)] + ' ' + pos[(i+4)])
#             print(temp)
        else:
            count += 1
            d_pos.append(temp)
            temp = []
            temp.append(pos[i] + ' ' + pos[(i+1)] + ' ' + pos[(i+2)] + ' ' + pos[(i+3)] + ' ' + pos[(i+4)])
#             print(temp)
    d_pos.append(temp)
    return d_pos
            
# d_pos = pos2dict(position)

In [34]:
def crf(data, pos, path): 
    if (os.path.isfile(path)):
        os.remove(path)
    outputfile = open(path, 'a', encoding= 'utf-8')
    
    
    for per in range(len(data)):
        temp = []
        count = -1
        flag = False
        for t in range(len(pos[per])):
            temp.append(pos[per][t].split()[1])
        
        for w in range(len(data[per])):
            if data[per][w] != ' ':
                if str(w) in temp and flag == False:
                    count += 1
                    outputfile.write(data[per][w] + '\t' + 'B-' + pos[per][count].split()[4] + '\n')
                    flag = True
                    if pos[per][count].split()[2] == str(w+1):
                        flag = False
                elif flag == True:
                    outputfile.write(data[per][w] + '\t' + 'I-' + pos[per][count].split()[4] + '\n')
                    if pos[per][count].split()[2] == str(w+1):
                        flag = False
                else:
                    outputfile.write(data[per][w] + '\t' + 'O' + '\n')
        outputfile.write('\n')
    outputfile.close()

In [35]:
def test_crf(data, path):
    if (os.path.isfile(path)):
        os.remove(path)
    outputfile = open(path, 'a', encoding= 'utf-8')
    
    for per in range(len(data)):
        for w in range(len(data[per])):
            if data[per][w] != ' ':
                outputfile.write(data[per][w] + '\tO\n')
        outputfile.write('\n')
    outputfile.close()

In [36]:
trainingset, position, mentions=loadInputFile(file_path)
position = pos2dict(position)
crf(trainingset, position, data_path)

In [ ]:
# print(position)

In [ ]:
testingset, tposition, tmentions=loadInputFile(test_path)
test_crf(testingset, tdata_path)

In [ ]:
# devset, dev_pos, dev_mentions = loadInputFile(dev_path)
# test_crf(devset, devpath)

In [ ]:
def word_type(data, path):
    if (os.path.isfile(path)):
        os.remove(path)
    outputfile = open(path, 'a', encoding= 'utf-8')
    
#     jieba.set_dictionary('dict.txt.big')
    
    for num in data:
        seg = psg.cut(num)
        
        for ele in seg:
            for w in str(ele.word):
                if w == ' ':
                    continue
                outputfile.write(w + '\t' + str(ele.flag) + '\n')
        
        outputfile.write('\n')
    outputfile.close()

In [ ]:
word_type(trainingset, train_type)

In [ ]:
word_type(testingset, test_type)

In [ ]:
# word_type(devset, dev_type)

In [28]:
def read(path, dtype):
    with open(path, 'r', encoding='utf-8') as f:
        data = f.readlines()
    f.close()
    
    with open(dtype, 'r', encoding='utf-8') as f:
        data_type = f.readlines()
    f.close()
    
    t = []
    for l in data_type:
        if l != '\n':
            t.append(l.split('\t'))
            
#     print(len(t))
    
    m = []
    for line in data:
        if line != '\n':
#             m.append(line.split('\t')[1].strip())
            m.append(line.split('\t'))
            
    for line in range(len(t)):
        if t[line][0] != m[line][0]:
            print(t[line][0])
            print(m[line][0])
            print(line)
            
#     print(len(m))
            
#     all_data = []
#     per = []
#     count = 0
#     for line in range(len(data)):
#         temp = []
#         if data[line] == '\n':
#             all_data.append(per)
#             per = []
#         else:
#             if count == 0:
#                 temp.append(t[count][0])
#                 temp.append(t[count][1].strip())
#                 temp.append(t[count][2].strip())   #在詞的位置
#                 temp.append(t[len(m)-1][0])   # 前一字
#                 temp.append(t[len(m)-1][1].strip())
#                 temp.append(t[count+1][0])   # 後一字
#                 temp.append(t[count+1][1].strip())
#                 temp.append(m[count])
#                 per.append(temp)
#                 count += 1
#             elif count == len(m)-1:
#                 temp.append(t[count][0])
#                 temp.append(t[count][1].strip())
#                 temp.append(t[count][2].strip())   #在詞的位置
#                 temp.append(t[count-1][0])   # 前一字
#                 temp.append(t[count-1][1].strip())
#                 temp.append(t[0][0])   # 後一字
#                 temp.append(t[0][1].strip())
#                 temp.append(m[count])
#                 per.append(temp)
#                 count+=1
#             else:
#                 temp.append(t[count][0])
#                 temp.append(t[count][1].strip())
#                 temp.append(t[count][2].strip())   #在詞的位置
#                 temp.append(t[count-1][0])   # 前一字
#                 temp.append(t[count-1][1].strip())
#                 temp.append(t[count+1][0])   # 後一字
#                 temp.append(t[count+1][1].strip())
#                 temp.append(m[count])
#                 per.append(temp)
#                 count+=1
#     return all_data

In [ ]:
# data_path='data/train1_hsin.data'
# tdata_path='data/test.data'
# devpath='data/dev.data'

# train_type = 'data/train.type'
# test_type = 'data/test.type'
# dev_type = 'data/dev.type'

In [29]:
train_data = read(data_path, train_type)
# test_data = read(dev_path)
test_data = read(tdata_path, test_type)
print('done')

。
A
4210
醫
1
4211
師
6
4212
：
0
4213
阿
0
4214
阿
7
4215
嬤
0
4216
她
5
4217
好
8
4218
像
3
4219
說
。
4220
有
醫
4221
，
師
4222
前
：
4223
天
阿
4224
又
阿
4225
有
嬤
4226
在
她
4227
發
好
4228
燒
像
4229
喔
說
4230
。
有
4231
家
，
4232
屬
前
4233
：
天
4234
對
又
4235
阿
有
4236
都
在
4237
，
發
4238
有
燒
4239
時
喔
4240
候
。
4241
都
家
4242
會
屬
4243
一
：
4244
天
對
4245
她
阿
4246
會
都
4247
燒
，
4248
，
有
4249
誒
時
4250
，
候
4251
可
都
4252
是
會
4253
她
一
4254
這
天
4255
樣
她
4256
前
會
4257
天
燒
4258
就
，
4259
燒
誒
4260
兩
，
4261
次
可
4262
了
是
4263
。
她
4264
醫
這
4265
師
樣
4266
：
前
4267
好
天
4268
，
就
4269
那
燒
4270
樣
兩
4271
不
次
4272
行
了
4273
家
醫
4275
屬
師
4276
下
好
4278
午
，
4279
誒
那
4280
，
樣
4281
昨
不
4282
天
行
4283
下
。
4284
午
家
4285
四
屬
4286
點
：
4287
一
下
4288
次
午
4289
，
誒
4290
然
，
4291
後
昨
4292
半
天
4293
夜
下
4294
一
午
4295
點
四
4296
半
點
4297
兩
一
4298
點
次
4299
那
，
4300
邊
然
4301
又
後
4302
燒
半
4303
到
夜
4304
3
一
4305
8
點
4306
.
半
4307
2
兩
4308
。
點
4309
醫
那
4310
師
邊
4311
：
又
4312
喔
燒
4313
，
到
4314
是
3
4315
是
8
4316
。
.
4317
家
2
4318
屬
。
4319
：
醫
4320
對
師
4321
。
：
4322
醫

有
來
5337
發
。
5338
燒
醫
5339
嗎
師
5340
？
：
5341
家
喔
5342
屬
她
5343
：
那
5344
沒
時
5345
發
候
5346
燒
有
5347
。
發
5348
醫
燒
5349
師
嗎
5350
：
？
5351
沒
家
5352
發
屬
5353
燒
：
5354
。
沒
5355
家
發
5356
屬
燒
5357
：
。
5358
有
醫
5359
，
師
5360
有
：
5361
一
沒
5362
兩
發
5363
次
燒
5364
都
。
5365
這
家
5366
樣
屬
5367
。
：
5368
醫
有
5369
師
，
5370
：
有
5371
還
一
5372
是
兩
5373
藥
次
5374
？
都
5375
家
這
5376
屬
樣
5377
：
。
5378
藥
醫
5379
，
師
5380
就
：
5381
藥
還
5382
喔
是
5383
？
藥
5384
醫
？
5385
師
家
5386
：
屬
5387
結
：
5388
核
藥
5389
菌
，
5390
是
就
5391
會
藥
5392
跑
喔
5393
啦
？
5394
，
醫
5395
會
師
5396
跑
：
5397
，
結
5398
有
核
5399
，
菌
5400
也
是
5401
有
會
5402
，
啦
5404
不
，
5405
過
會
5406
那
跑
5407
比
，
5408
例
有
5409
也
，
5410
很
也
5411
低
有
5412
。
跑
5413
家
，
5414
屬
不
5415
：
過
5416
好
那
5417
。
比
5418
醫
例
5419
師
也
5420
：
很
5421
阿
低
5422
但
。
5423
是
家
5424
也
屬
5425
是
：
5426
一
好
5427
樣
。
5428
也
醫
5429
是
師
5430
吃
：
5431
藥
阿
5432
阿
但
5433
呵
是
5434
～
也
5435
民
是
5436
眾
一
5437
：
樣
5438
阿
也
5439
就
是
5440
，
藥
5442
也
阿
5443
是
呵
5444
吃
～
5445
藥
民
5446
這
眾
5447
樣
：
5448
嗎
阿
5449
？

不
6363
就
多
6364
做
第
6365
半
，
6366
個
第
6367
小
一
6368
時
個
6369
到
小
6370
三
時
6371
十
…
6372
，
…
6373
一
就
6374
…
做
6375
…
半
6376
一
個
6377
個
小
6378
小
時
6379
時
到
6380
啦
三
6381
。
十
6382
家
，
6383
屬
一
6384
：
…
6385
恩
…
6386
。
一
6387
醫
個
6388
師
小
6389
：
時
6390
阿
啦
6391
然
。
6392
後
家
6393
，
屬
6394
其
：
6395
實
恩
6396
這
。
6397
，
醫
6398
她
師
6399
用
：
6400
頭
阿
6401
皮
然
6402
針
後
6403
她
，
6404
個
其
6405
小
實
6406
的
這
6407
有
，
6408
時
她
6409
候
用
6410
打
頭
6411
完
皮
6412
…
針
6413
…
她
6414
民
個
6415
眾
小
6416
：
的
6417
不
有
6418
安
時
6419
全
候
6420
。
打
6421
醫
完
6422
師
…
6423
：
…
6424
阿
民
6425
怕
眾
6426
埋
：
6427
針
不
6428
是
安
6429
不
全
6430
是
。
6431
？
醫
6432
民
師
6433
眾
：
6434
：
阿
6435
對
怕
6436
我
埋
6437
想
針
6438
叫
是
6439
他
不
6440
埋
是
6441
，
？
6442
因
民
6443
…
眾
6444
…
：
6445
因
對
6446
為
我
6447
他
想
6448
禮
叫
6449
拜
他
6450
一
埋
6451
禮
，
6452
拜
因
6453
二
…
6454
沒
…
6455
開
因
6456
。
為
6457
醫
他
6458
師
禮
6459
：
拜
6460
喔
一
6461
，
禮
6462
阿
拜
6463
你
二
6464
們
沒
6465
要
開
6466
自
。
6467
己
醫
6468
加
師
6469
，
：
6470
你
喔
6471
們
，
6472
會
阿
6473
自
你

7348
對
嗎
7349
稱
？
7350
阿
要
7351
。
不
7352
民
然
7353
眾
應
7354
：
該
7355
對
是
7356
。
左
7357
醫
右
7358
師
對
7359
：
稱
7360
這
阿
7361
裡
。
7362
就
民
7363
是
眾
7364
腫
：
7365
起
對
7366
來
。
7367
化
醫
7368
膿
師
7369
在
：
7370
裡
這
7371
面
裡
7372
。
就
7373
民
是
7374
眾
腫
7375
：
起
7376
就
來
7377
是
化
7378
開
膿
7379
刀
在
7380
開
裡
7381
在
面
7382
右
。
7383
邊
民
7384
大
眾
7385
腿
：
7386
後
就
7387
側
是
7388
吧
開
7389
？
刀
7390
醫
開
7391
師
在
7392
：
右
7393
對
邊
7394
，
大
7395
你
腿
7396
那
後
7397
個
側
7398
傷
吧
7399
口
？
7400
很
醫
7401
深
師
7402
，
：
7403
那
對
7404
止
，
7405
痛
你
7406
藥
那
7407
這
個
7408
樣
傷
7409
可
口
7410
以
很
7411
嗎
深
7412
？
，
7413
民
那
7414
眾
止
7415
：
痛
7416
可
藥
7417
以
這
7418
。
樣
7419
醫
可
7420
師
以
7421
：
嗎
7422
可
？
7423
以
民
7424
啦
眾
7425
齁
：
7426
，
可
7427
那
以
7428
個
。
7429
要
醫
7430
這
師
7431
樣
：
7432
藥
可
7433
這
以
7434
樣
啦
7435
吃
齁
7436
是
，
7437
還
那
7438
可
個
7439
以
要
7440
？
這
7441
民
樣
7442
眾
藥
7443
：
這
7444
可
樣
7445
以
吃
7446
的
是
7447
。
還
7448
醫
可
7449
師
以
7450
：
？
7451
那
民
7452
是
眾
7453
很
：
7454
好
可
7455
的
以
7456
藥
的
7457
，
。
7458
那
醫
7

8539
了
理
8540
。
師
8541
醫
：
8542
師
那
8543
：
樣
8544
那
這
8545
個
邊
8546
是
就
8547
回
可
8548
診
以
8549
單
了
8550
謝
那
8555
謝
個
8556
你
是
8557
這
回
8558
樣
診
8559
幫
單
8560
忙
。
8561
他
醫
8562
們
師
8563
這
：
8564
樣
謝
8565
，
謝
8566
那
你
8567
最
這
8568
近
樣
8569
還
幫
8570
好
忙
8571
嗎
他
8572
？
們
8573
民
這
8574
眾
樣
8575
：
，
8576
就
那
8577
是
最
8578
因
近
8579
為
還
8580
不
好
8581
太
嗎
8582
好
？
8583
所
民
8584
以
眾
8585
才
：
8586
要
就
8587
再
是
8588
回
因
8589
診
為
8590
，
不
8591
因
太
8592
為
好
8593
我
所
8594
為
以
8595
甚
才
8596
麼
要
8597
決
再
8598
定
回
8599
今
診
8600
天
，
8601
要
因
8602
來
為
8603
回
我
8604
診
為
8605
，
甚
8606
是
麼
8607
因
決
8608
為
定
8609
我
今
8610
大
天
8611
概
要
8612
應
來
8613
該
回
8614
是
診
8615
有
，
8616
持
是
8617
續
因
8618
三
為
8619
個
我
8620
禮
大
8621
拜
概
8622
，
應
8623
就
該
8624
覺
是
8625
得
有
8626
排
持
8627
尿
續
8628
是
三
8629
有
個
8630
一
禮
8631
點
拜
8632
點
，
8633
不
就
8634
是
覺
8635
這
得
8636
麼
排
8637
的
尿
8638
舒
是
8639
服
有
8640
。
一
8641
醫
點
8642
師
點
8643
：
不
8644
舒
是
8645
服
這
8646
這
麼
8647
樣
的
8648
。
舒
8649
民
服
8650
眾
。
8651
：
醫
8652
對
師
8653
，
：
8

...

179359
可
別
179360
能
。
179361
暴
民
179362
露
眾
179363
到
：
179364
病
就
179365
毒
是
179366
之
會
179367
前
卡
179368
我
很
179369
們
多
179370
先
。
179371
讓
醫
179372
身
師
179373
體
：
179374
有
卡
179375
些
很
179376
治
久
179377
療
嘛
179378
藥
。
179379
物
民
179380
的
眾
179381
濃
：
179382
度
對
179383
，
啊
179384
那
就
179385
如
是
179386
果
。
179387
治
醫
179388
療
師
179389
，
：
179390
等
對
179391
於
啊
179392
說
。
179393
如
民
179394
果
眾
179395
在
：
179396
性
好
179397
行
好
179398
為
笑
179399
的
。
179400
過
醫
179401
程
師
179402
中
：
179403
有
好
179404
幾
喔
179405
隻
那
179406
病
就
179407
毒
這
179408
跑
樣
179409
進
囉
179410
來
。
179411
的
民
179412
的
眾
179413
話
：
179414
，
那
179415
那
就
179416
就
五
179417
可
個
179418
以
月
179419
有
後
179420
、
再
179421
有
介
179422
等
紹
179423
於
。
179424
說
醫
179425
把
師
179426
這
：
179427
個
你
179428
病
要
179429
毒
先
179430
殺
開
179431
在
抽
179432
身
血
179433
體
單
179434
的
嗎
179435
外
？
179436
面
民
179437
減
眾
179438
少
：
179439
感
好
179440
染
。
179441
的
醫
179442
機
師
179443
會
：
179444
啦
先
179445
，
開
179446
所
抽
179447
以
血
179448
概
單
179449
念
那

管
也
180125
對
是
180126
象
晚
180127
是
上
180128
認
8
180129
識
點
180130
或
吃
180131
不
藥
180132
認
後
180133
識
天
180134
都
也
180135
一
是
180136
定
8
180137
會
點
180138
戴
吃
180139
？
藥
180140
民
。
180141
眾
民
180142
：
眾
180143
對
：
180144
。
恩
180145
醫
。
180146
師
醫
180147
：
師
180148
是
：
180149
1
他
180150
0
原
180151
會
則
180152
帶
上
180153
還
是
180154
是
這
180155
6
樣
180156
9
啦
180157
也
，
180158
會
那
180159
戴
我
180160
？
覺
180161
民
得
180162
眾
這
180163
：
兩
180164
沒
種
180165
有
各
180166
在
有
180167
6
好
180168
9
壞
180169
。
處
180170
醫
，
180171
師
可
180172
：
能
180173
沒
要
180174
有
看
180175
在
每
180176
6
個
180177
9
人
180178
，
的
180179
所
方
180180
以
法
180181
是
，
180182
1
每
180183
0
個
180184
的
人
180185
時
的
180186
候
生
180187
都
活
180188
一
型
180189
定
態
180190
會
拉
180191
戴
吼
180192
。
，
180193
民
第
180194
眾
一
180195
：
個
180196
嘿
是
180197
。
你
180198
醫
現
180199
師
在
180200
：
有
180201
所
固
180202
以
定
180203
是
的
180204
你
伴
180205
會
侶
180206
要
嗎
180207
求
？
180208
對
民
180209
方
眾
180210
戴
：
180211
。
沒
180212
民
有
180213
眾
。
180214
：
醫
180215

概
181132
服
是
181133
啊
這
181134
吼
樣
181135
，
。
181136
少
民
181137
數
眾
181138
有
：
181139
一
好
181140
些
。
181141
人
醫
181142
剛
師
181143
開
：
181144
始
那
181145
吃
所
181146
的
以
181147
時
你
181148
候
…
181149
會
…
181150
有
額
181151
一
你
181152
點
大
181153
點
概
181154
就
平
181155
是
均
181156
，
兩
181157
額
個
181158
…
月
181159
…
會
181160
可
有
181161
能
幾
181162
噁
次
181163
心
的
181164
感
這
181165
和
個
181166
肚
性
181167
子
行
181168
怪
為
181169
怪
？
181170
的
民
181171
，
眾
181172
但
：
181173
是
零
181174
不
到
181175
會
一
181176
真
次
181177
的
，
181178
影
醫
181179
響
師
181180
食
：
181181
慾
零
181182
或
到
181183
、
一
181184
或
次
181185
怎
，
181186
樣
所
181187
啦
以
181188
吼
真
181189
，
的
181190
那
很
181191
研
少
181192
究
呢
181193
上
！
181194
大
民
181195
概
眾
181196
會
：
181197
發
對
181198
現
阿
181199
有
。
181200
一
醫
181201
些
師
181202
人
：
181203
吃
好
181204
藥
，
181205
之
所
181206
後
以
181207
腎
零
181208
臟
到
181209
指
一
181210
數
次
181211
會
，
181212
有
所
181213
一
以
181214
點
你
181215
增
可
181216
加
能
181217
，
就
181218
骨
會
181219
質
m
181220
密
a
181221
度
y
181222
會

：
181972
能
這
181973
是
就
181974
這
很
181975
樣
難
181976
子
說
181977
不
我
181979
然
們
181980
這
現
181981
個
在
181982
大
當
181983
概
然
181984
就
發
181985
是
出
181986
一
去
181987
個
的
181988
月
藥
181989
可
大
181990
能
概
181991
還
都
181992
是
有
181993
還
一
181994
是
到
181995
五
兩
181996
千
年
181997
塊
的
181998
到
效
181999
五
期
182000
千
拉
182001
五
嘿
182002
百
。
182003
塊
民
182004
左
眾
182005
右
：
182006
拉
好
182007
，
好
182008
好
。
182009
所
醫
182010
以
師
182011
概
：
182012
念
那
182013
上
所
182014
是
以
182015
這
確
182016
樣
實
182017
子
是
182018
。
如
182019
民
果
182020
眾
放
182021
：
到
182022
恩
過
182023
。
期
182024
醫
了
182025
師
的
182026
：
這
182027
好
個
182028
，
疑
182029
那
慮
182030
…
，
182031
…
那
182032
反
當
182033
正
然
182034
這
能
182035
個
買
182036
我
學
182037
們
名
182038
可
藥
182039
以
好
182040
下
，
182041
次
因
182042
再
為
182043
來
反
182044
討
正
182045
論
買
182046
，
學
182047
那
名
182048
或
藥
182049
者
他
182050
是
價
182051
說
格
182052
我
會
182053
們
再
182054
在
、
182055
這
再
182056
一
等
182057
個
於
182058
禮
是
182059
拜
說
182060
內
他
182061
有
這
182062
拿
樣
182063
到

KeyboardInterrupt: 

In [ ]:
# print(train_data[0])

In [ ]:
def word2features(sent, i):
    word = sent[i][0]
    postag = sent[i][1]
    pos = sent[i][2]
    front = sent[i][3]
    front_tag = sent[i][4]
    back = sent[i][5]
    back_tag = sent[i][6]
    
    features = [
        'bias',
        'word=' + word,
        'word.islower={}'.format(word.islower()),
        'word.isupper={}'.format(word.isupper()),
        'word.isdigit={}'.format(word.isdigit()),
        'postag=' + postag,
        'postag[:2]=' + postag[:2],
        'pos=' + pos,
        'front=' + front,
        'front_tag=' + front_tag,
        'front_tag[:2]=' + front_tag[:2],
        'back=' + back,
        'back_tag=' + back_tag,
        'back_tag[:2]=' + back_tag[:2],
    ]
    if i > 0:
        word1 = sent[i-1][0]
        words = word1 + word
        features.extend([
            '-1:word=' + word1,
            '-1:words=' + words,
            '-1:word.isupper={}'.format(word1.isupper()),
            '-1:word.isdigit={}'.format(word1.isdigit()),
            '-1:postag=' + postag,
            '-1:postag[:2]=' + postag[:2],
            '-1:pos=' + pos,
            '-1:front=' + front,
            '-1:front_tag=' + front_tag,
            '-1:front_tag[:2]=' + front_tag[:2],
            '-1:back=' + back,
            '-1:back_tag=' + back_tag,
            '-1:back_tag[:2]=' + back_tag[:2],
        ])
    else:
        features.append('BOS')
        
    if i > 1:
        word1 = sent[i - 2][0]
        word2 = sent[i - 1][0]
        words = word1 + word2 + word
        features.extend([
            '-2:word=' + word1,
            '-2:words=' + words,
            '-2:word.isupper={}'.format(word1.isupper()),
            '-2:word.isdigit={}',format(word1.isdigit()),
            '-2:postag=' + postag,
            '-2:postag[:2]=' + postag[:2],
            '-2:pos=' + pos,
            '-2:front=' + front,
            '-2:front_tag=' + front_tag,
            '-2:front_tag[:2]=' + front_tag[:2],
            '-2:back=' + back,
            '-2:back_tag=' + back_tag,
            '-2:back_tag[:2]=' + back_tag[:2],
        ])
    if i > 2:
        word1 = sent[i - 3][0]
        word2 = sent[i - 2][0]
        word3 = sent[i - 1][0]
        words = word1 + word2 + word3 + word
        features.extend([
            '-3:word=' + word1,
            '-3:words=' + words,
            '-3:word.isupper={}'.format(word1.isupper()),
            '-3:word.isdigit={}',format(word1.isdigit()),
            '-3:postag=' + postag,
            '-3:postag[:2]=' + postag[:2],
            '-3:pos=' + pos,
            '-3:front=' + front,
            '-3:front_tag=' + front_tag,
            '-3:front_tag[:2]=' + front_tag[:2],
            '-3:back=' + back,
            '-3:back_tag=' + back_tag,
            '-3:back_tag[:2]=' + back_tag[:2],
        ])
    
    if i < len(sent) - 1:
        word1 = sent[i+1][0]
        words = word + word1
        features.extend([
            '+1:word=' + word1,
            '+1:words=' + words,
            '+1:word.isupper={}'.format(word1.isupper()),
            '+1:word.isdigit={}'.format(word1.isdigit()),
            '+1:postag=' + postag,
            '+1:postag[:2]=' + postag[:2],
            '+1:pos=' + pos,
            '+1:front=' + front,
            '+1:front_tag=' + front_tag,
            '+1:front_tag[:2]=' + front_tag[:2],
            '+1:back=' + back,
            '+1:back_tag=' + back_tag,
            '+1:back_tag[:2]=' + back_tag[:2],
        ])
    else:
        features.append('BOS')
        
    if i < len(sent) - 2:
        word1 = sent[i+2][0]
        word2 = sent[i+1][0]
        words = word + word1 + word2
        features.extend([
            '+2:word=' + word1,
            '+2:words=' + words,
            '+2:word.isupper={}'.format(word1.isupper()),
            '+2:word.isdigit={}'.format(word1.isdigit()),
            '+2:postag=' + postag,
            '+2:postag[:2]=' + postag[:2],
            '+2:pos=' + pos,
            '+2:front=' + front,
            '+2:front_tag=' + front_tag,
            '+2:front_tag[:2]=' + front_tag[:2],
            '+2:back=' + back,
            '+2:back_tag=' + back_tag,
            '+2:back_tag[:2]=' + back_tag[:2],
        ])
    if i < len(sent) - 3:
        word1 = sent[i+3][0]
        word2 = sent[i+2][0]
        word3 = sent[i+1][0]
        words = word + word1 + word2 + word3
        features.extend([
            '+3:word=' + word1,
            '+3:words=' + words,
            '+3:word.isupper={}'.format(word1.isupper()),
            '+3:word.isdigit={}'.format(word1.isdigit()),
            '+3:postag=' + postag,
            '+3:postag[:2]=' + postag[:2],
            '+3:pos=' + pos,
            '+3:front=' + front,
            '+3:front_tag=' + front_tag,
            '+3:front_tag[:2]=' + front_tag[:2],
            '+3:back=' + back,
            '+3:back_tag=' + back_tag,
            '+3:back_tag[:2]=' + back_tag[:2],
        ])
        
    return features

In [ ]:
def sent2feature(sent):
    return [word2features(sent, i) for i in range(len(sent))]

In [ ]:
def sent2label(sent):
    return [label for word, tag,pos, front, front_tag, back, back_tag, label in sent]

In [ ]:
def sent2word(sent):
    return [word for word, tag,pos, front, front_tag, back, back_tag, label in sent]

In [ ]:
X_train = [sent2feature(s) for s in train_data]
Y_train = [sent2label(s) for s in train_data]

In [ ]:
X_test = [sent2feature(a) for a in test_data]
# Y_test = [sent2label(a) for a in test_data]

In [ ]:
import sklearn_crfsuite

crf = sklearn_crfsuite.CRF(
    algorithm='lbfgs',
    c1=0.1,
    c2=0.1,
    max_iterations=500,
    all_possible_transitions=True
)
crf.fit(X_train, Y_train)


In [ ]:
from sklearn_crfsuite import scorers
from sklearn_crfsuite import metrics
y_pred = crf.predict(X_test)
# metrics.flat_f1_score(Y_test, y_pred,
#                       average='weighted')

In [ ]:
# print(y_pred)

In [ ]:
output="article_id\tstart_position\tend_position\tentity_text\tentity_type\n"
for test_id in range(len(y_pred)):
    pos=0
    start_pos=None
    end_pos=None
    entity_text=None
    entity_type=None
    for pred_id in range(len(y_pred[test_id])):
        if y_pred[test_id][pred_id][0]=='B':
            start_pos=pos
            entity_type=y_pred[test_id][pred_id][2:]
        elif start_pos is not None and y_pred[test_id][pred_id][0]=='I' and y_pred[test_id][pred_id+1][0]=='O':
            end_pos=pos
            entity_text=''.join([test_data[test_id][position][0] for position in range(start_pos,end_pos+1)])
            line=str(test_id)+'\t'+str(start_pos)+'\t'+str(end_pos+1)+'\t'+entity_text+'\t'+entity_type
            output+=line+'\n'
        pos+=1     

In [ ]:
output_path='output.tsv'
with open(output_path,'w',encoding='utf-8') as f:
    f.write(output)